In [5]:
# 必要なライブラリのインポート
import pandas as pd
from google.colab import drive
import datetime

# Google Driveのマウント
drive.mount('/content/drive', force_remount=True)

# Google Driveのマイドライブからファイルを読み込む
timecard_df = pd.read_csv("/content/drive/My Drive/C-United_file/Gulf.csv")
hcpa_list_df = pd.read_csv("/content/drive/My Drive/C-United_file/HCPA_list.csv")

# 勤務店舗カラムに「ヘルプ」が含まれるレコードを抽出
timecard_df = timecard_df.dropna(subset=['勤務店舗'])
timecard_df = timecard_df[timecard_df['勤務店舗'].str.contains('ヘルプ')]

# 必要なカラムを選択
selected_columns = timecard_df.columns[[0, 1, 4, 24, 26, 32]]
timecard_selected_df = timecard_df[selected_columns]

# 労働時間が空欄の行を削除
timecard_selected_df = timecard_selected_df.dropna(subset=['労働時間'])

# 労働時間の値を60で割って「時間」単位に変更
timecard_selected_df['労働時間'] = timecard_selected_df['労働時間'] / 60

# 残業時間の値を60で割って「時間」単位に変更
timecard_selected_df['残業時間'] = timecard_selected_df['残業時間'] / 60

# 新しいカラムを挿入
timecard_selected_df.insert(3, "HCPコード", "")
timecard_selected_df.insert(4, "勤務日数", 0)

# カラム名を変更
timecard_selected_df.columns = ['月度', '店舗コード', '従業員コード', 'HCPコード', '勤務日数', '労働時間', '残業時間', '所属店舗コード']

# 従業員コードでグループ化して勤務日数をカウント
grouped_df = timecard_selected_df.groupby(['月度', '店舗コード', '従業員コード', '所属店舗コード']).agg({
    '労働時間': 'sum',
    '残業時間': 'sum',
    '勤務日数': 'size'
}).reset_index()

# HCPコードを設定
grouped_df['HCPコード'] = grouped_df['従業員コード'].apply(lambda x: 'HCP' if x in hcpa_list_df['HCPコード'].values else '')

# 現在の日付を取得
current_date = datetime.datetime.now().strftime('%Y%m%d')

# 加工されたデータをCSVファイルに保存
output_path = f"/content/drive/My Drive/C-United_file/Gulf_help_{current_date}.csv"
grouped_df.to_csv(output_path, index=False)



Mounted at /content/drive
